## 1. 환경설정

In [1]:
# !pip install interpret

In [2]:
import pandas as pd
from lightgbm import LGBMRegressor

## 2. 데이터 로드

In [3]:
df = pd.read_csv("data.csv", encoding='ansi')
df

연번    연도  월  주차         공개일     조사기간(S)     조사기간(F)    긍정    부정  잘모름  \
0      1  2012  1   1  2012-01-06  2012-01-02  2012-01-06  26.0  63.0   11   
1      2  2012  1   2  2012-01-13  2013-01-09  2012-01-13  24.0  65.0   11   
2      3  2012  1   3  2012-01-20  2012-01-16  2012-01-20  22.0  65.0   13   
3      4  2012  1   4  2012-01-27  2012-01-25  2012-01-27  24.0  64.0   12   
4      5  2012  2   1         NaN  2012-01-30  2012-02-03  22.0  65.0   13   
..   ...   ... ..  ..         ...         ...         ...   ...   ...  ...   
606  607  2023  8   1  2023-08-04  2023-08-01  2023-08-03  33.0  56.0   11   
607  608  2023  8   2  2023-08-11  2023-08-08  2023-08-10  35.0  57.0    8   
608  609  2023  8   3         미실시  2023-08-15  2023-08-17   NaN   NaN  100   
609  610  2023  8   4  2023-08-25  2023-08-22  2023-08-24  34.0  57.0    9   
610  611  2023  8   5  2023-09-01  2023-08-29  2023-08-31  33.0  59.0    8   

     ...        국제%    북한_외교%        문화%        사회%     사건_사고%        정치%  \
0    ...   9.953095  3.866834  13.980094  13.259352   8.763299  11.943714   
1    ...  11.818475  3.075600  12.216367  13.237983   8.506291  12.345413   
2    ...  12.098789  2.402460  12.118009  13.213531   8.591197  12.742648   
3    ...  13.525856  3.102754  12.397582  13.472129   8.623237  10.100739   
4    ...  10.338562  2.247513  13.274675  13.771997   8.645754  11.027161   
..   ...        ...       ...        ...        ...        ...        ...   
606  ...  10.009558  2.710922   7.863411  18.463811   8.523764  10.278912   
607  ...  10.478589  1.410579   7.867338  15.633921  12.216625   8.413098   
608  ...  12.550154  3.965662   8.967062  14.817580   9.452272  10.711953   
609  ...  13.380852  6.415033   7.297910  13.672445  11.501701   9.881743   
610  ...  12.694787  2.782084   8.411520  13.641185  10.777515  13.045607   

         스포츠%        지역%  기타(날씨, 미분류)%   퍼센트합  
0    6.475232   6.784121      5.880334  100.0  
1    6.538337   6.645876      5.871599  100.0  
2    6.409764   7.120892      6.515472  100.0  
3    6.662189   6.675621      6.836803  100.0  
4    7.067712   7.096404      6.685157  100.0  
..        ...        ...           ...    ...  
606  4.674602  13.293944      7.846034    NaN  
607  3.912678  13.853904     12.418136    NaN  
608  4.404218  13.473920      6.662312    NaN  
609  4.122793  12.214482      5.451158    NaN  
610  3.875337  12.278698      5.498899    NaN  

[611 rows x 34 columns]

In [4]:
df.columns

Index(['연번', '연도', '월', '주차', '공개일', '조사기간(S)', '조사기간(F)', '긍정', '부정', '잘모름',
       '과학_IT', '경제', '국제', '북한_외교', '문화', '사회', '사건_사고', '정치', '스포츠', '지역',
       '기타(날씨, 미분류)', '주간합', '과학_IT%', '경제%', '국제%', '북한_외교%', '문화%', '사회%',
       '사건_사고%', '정치%', '스포츠%', '지역%', '기타(날씨, 미분류)%', '퍼센트합'],
      dtype='object')

### 2.1. 전처리

In [5]:
# 필요한 열만 추출

df_train = df.loc[:,['연도', '월', '주차', '긍정', '부정', '잘모름',
       '과학_IT', '경제', '국제', '북한_외교', '문화', '사회', '사건_사고', '정치', '스포츠', '지역',
       '기타(날씨, 미분류)', '주간합', '과학_IT%', '경제%', '국제%', '북한_외교%', '문화%', '사회%',
       '사건_사고%', '정치%', '스포츠%', '지역%', '기타(날씨, 미분류)%']]

df_train

연도  월  주차    긍정    부정  잘모름  과학_IT    경제    국제  북한_외교  ...        경제%  \
0    2012  1   1  26.0  63.0   11    334  1335   870    338  ...  15.272852   
1    2012  1   2  24.0  65.0   11    372  1464  1099    286  ...  15.743628   
2    2012  1   3  22.0  65.0   13    455  1500  1259    250  ...  14.414761   
3    2012  1   4  24.0  64.0   12    319  1066  1007    231  ...  14.318334   
4    2012  2   1  22.0  65.0   13    447  1628  1081    235  ...  15.570008   
..    ... ..  ..   ...   ...  ...    ...   ...   ...    ...  ...        ...   
606  2023  8   1  33.0  56.0   11    418  1462  1152    312  ...  12.703102   
607  2023  8   2  35.0  57.0    8    399  1244  1248    168  ...  10.445004   
608  2023  8   3   NaN   NaN  100    362  1245  1345    425  ...  11.617057   
609  2023  8   4  34.0  57.0    9    486  1497  1652    792  ...  12.125385   
610  2023  8   5  33.0  59.0    8    481  1602  1556    341  ...  13.070082   

           국제%    북한_외교%        문화%        사회%     사건_사고%        정치%  \
0     9.953095  3.866834  13.980094  13.259352   8.763299  11.943714   
1    11.818475  3.075600  12.216367  13.237983   8.506291  12.345413   
2    12.098789  2.402460  12.118009  13.213531   8.591197  12.742648   
3    13.525856  3.102754  12.397582  13.472129   8.623237  10.100739   
4    10.338562  2.247513  13.274675  13.771997   8.645754  11.027161   
..         ...       ...        ...        ...        ...        ...   
606  10.009558  2.710922   7.863411  18.463811   8.523764  10.278912   
607  10.478589  1.410579   7.867338  15.633921  12.216625   8.413098   
608  12.550154  3.965662   8.967062  14.817580   9.452272  10.711953   
609  13.380852  6.415033   7.297910  13.672445  11.501701   9.881743   
610  12.694787  2.782084   8.411520  13.641185  10.777515  13.045607   

         스포츠%        지역%  기타(날씨, 미분류)%  
0    6.475232   6.784121      5.880334  
1    6.538337   6.645876      5.871599  
2    6.409764   7.120892      6.515472  
3    6.662189   6.675621      6.836803  
4    7.067712   7.096404      6.685157  
..        ...        ...           ...  
606  4.674602  13.293944      7.846034  
607  3.912678  13.853904     12.418136  
608  4.404218  13.473920      6.662312  
609  4.122793  12.214482      5.451158  
610  3.875337  12.278698      5.498899  

[611 rows x 29 columns]

In [6]:
# 데이터 셋 체크

df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 611 entries, 0 to 610
Data columns (total 29 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   연도            611 non-null    int64  
 1   월             611 non-null    int64  
 2   주차            611 non-null    int64  
 3   긍정            538 non-null    float64
 4   부정            538 non-null    float64
 5   잘모름           611 non-null    int64  
 6   과학_IT         611 non-null    int64  
 7   경제            611 non-null    int64  
 8   국제            611 non-null    int64  
 9   북한_외교         611 non-null    int64  
 10  문화            611 non-null    int64  
 11  사회            611 non-null    int64  
 12  사건_사고         611 non-null    int64  
 13  정치            611 non-null    int64  
 14  스포츠           611 non-null    int64  
 15  지역            611 non-null    int64  
 16  기타(날씨, 미분류)   611 non-null    int64  
 17  주간합           611 non-null    int64  
 18  과학_IT%        611 non-null    

약 73주치 데이터 손실

전체 데이터 611건 중 73주치 데이터 손실

538건 데이터 활용 가능

In [7]:
# null 값 채우기
df_clean = df_train.fillna(0)
df_clean.describe()

연도           월          주차          긍정          부정  \
count   611.000000  611.000000  611.000000  611.000000  611.000000   
mean   2017.340426    6.445172    2.708674   38.346972   40.088380   
std       3.374735    3.437239    1.275330   19.839373   20.345025   
min    2012.000000    1.000000    1.000000    0.000000    0.000000   
25%    2014.000000    3.000000    2.000000   29.000000   26.500000   
50%    2017.000000    6.000000    3.000000   40.000000   46.000000   
75%    2020.000000    9.000000    4.000000   48.000000   55.000000   
max    2023.000000   12.000000    5.000000   84.000000   93.000000   

              잘모름       과학_IT           경제           국제        북한_외교  ...  \
count  611.000000  611.000000   611.000000   611.000000   611.000000  ...   
mean    21.564648  447.004910  1424.198036  1201.700491   471.726678  ...   
std     29.215710  119.105567   329.692835   300.657226   273.195124  ...   
min      3.000000  144.000000   459.000000   316.000000   105.000000  ...   
25%      8.000000  358.000000  1161.000000  1006.000000   290.000000  ...   
50%     10.000000  445.000000  1446.000000  1152.000000   399.000000  ...   
75%     14.000000  525.000000  1672.500000  1356.000000   585.000000  ...   
max    100.000000  913.000000  2402.000000  2958.000000  2896.000000  ...   

              경제%         국제%      북한_외교%         문화%         사회%      사건_사고%  \
count  611.000000  611.000000  611.000000  611.000000  611.000000  611.000000   
mean    13.332254   11.315574    4.557031   12.932907   13.533115    8.078357   
std      1.800079    2.087071    2.672817    4.108673    2.656315    1.647299   
min      7.534083    7.729514    1.212983    6.465931    8.023142    2.840909   
25%     12.104833    9.928503    2.733055    9.669703   11.694202    6.994063   
50%     13.337530   11.045752    3.893724   12.096019   13.019488    7.942318   
75%     14.465869   12.252532    5.553908   15.016035   14.708250    9.059974   
max     18.822496   24.070993   22.282130   28.566052   26.233806   13.448985   

              정치%        스포츠%         지역%  기타(날씨, 미분류)%  
count  611.000000  611.000000  611.000000    611.000000  
mean    12.893038    5.921987    8.076076      5.178689  
std      4.000452    2.352242    2.745493      1.060880  
min      6.022727    3.094855    3.303303      3.061679  
25%     10.539793    4.422173    6.110021      4.430945  
50%     12.131716    5.172414    6.957756      5.040414  
75%     14.165800    7.070410   10.607597      5.730082  
max     37.658455   22.753308   20.788838     12.418136  

[8 rows x 29 columns]

In [8]:
## 확인
df_clean.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 611 entries, 0 to 610
Data columns (total 29 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   연도            611 non-null    int64  
 1   월             611 non-null    int64  
 2   주차            611 non-null    int64  
 3   긍정            611 non-null    float64
 4   부정            611 non-null    float64
 5   잘모름           611 non-null    int64  
 6   과학_IT         611 non-null    int64  
 7   경제            611 non-null    int64  
 8   국제            611 non-null    int64  
 9   북한_외교         611 non-null    int64  
 10  문화            611 non-null    int64  
 11  사회            611 non-null    int64  
 12  사건_사고         611 non-null    int64  
 13  정치            611 non-null    int64  
 14  스포츠           611 non-null    int64  
 15  지역            611 non-null    int64  
 16  기타(날씨, 미분류)   611 non-null    int64  
 17  주간합           611 non-null    int64  
 18  과학_IT%        611 non-null    

In [9]:
## 학습용 데이터 셋 저장

df_clean.to_csv("data_clean.csv",encoding = 'cp949',index = False)

## 3. 모델링 진행

In [10]:
df = pd.read_csv("data_clean.csv",encoding = 'cp949')
df

연도  월  주차    긍정    부정  잘모름  과학_IT    경제    국제  북한_외교  ...        경제%  \
0    2012  1   1  26.0  63.0   11    334  1335   870    338  ...  15.272852   
1    2012  1   2  24.0  65.0   11    372  1464  1099    286  ...  15.743628   
2    2012  1   3  22.0  65.0   13    455  1500  1259    250  ...  14.414761   
3    2012  1   4  24.0  64.0   12    319  1066  1007    231  ...  14.318334   
4    2012  2   1  22.0  65.0   13    447  1628  1081    235  ...  15.570008   
..    ... ..  ..   ...   ...  ...    ...   ...   ...    ...  ...        ...   
606  2023  8   1  33.0  56.0   11    418  1462  1152    312  ...  12.703102   
607  2023  8   2  35.0  57.0    8    399  1244  1248    168  ...  10.445004   
608  2023  8   3   0.0   0.0  100    362  1245  1345    425  ...  11.617057   
609  2023  8   4  34.0  57.0    9    486  1497  1652    792  ...  12.125385   
610  2023  8   5  33.0  59.0    8    481  1602  1556    341  ...  13.070082   

           국제%    북한_외교%        문화%        사회%     사건_사고%        정치%  \
0     9.953095  3.866834  13.980094  13.259352   8.763299  11.943714   
1    11.818475  3.075600  12.216367  13.237983   8.506291  12.345413   
2    12.098789  2.402460  12.118009  13.213531   8.591197  12.742648   
3    13.525856  3.102754  12.397582  13.472129   8.623237  10.100739   
4    10.338562  2.247513  13.274675  13.771997   8.645754  11.027161   
..         ...       ...        ...        ...        ...        ...   
606  10.009558  2.710922   7.863411  18.463811   8.523764  10.278912   
607  10.478589  1.410579   7.867338  15.633921  12.216625   8.413098   
608  12.550154  3.965662   8.967062  14.817580   9.452272  10.711953   
609  13.380852  6.415033   7.297910  13.672445  11.501701   9.881743   
610  12.694787  2.782084   8.411520  13.641185  10.777515  13.045607   

         스포츠%        지역%  기타(날씨, 미분류)%  
0    6.475232   6.784121      5.880334  
1    6.538337   6.645876      5.871599  
2    6.409764   7.120892      6.515472  
3    6.662189   6.675621      6.836803  
4    7.067712   7.096404      6.685157  
..        ...        ...           ...  
606  4.674602  13.293944      7.846034  
607  3.912678  13.853904     12.418136  
608  4.404218  13.473920      6.662312  
609  4.122793  12.214482      5.451158  
610  3.875337  12.278698      5.498899  

[611 rows x 29 columns]

In [11]:
## 미조사 데이터 제외
df_clean = df.loc[df['긍정'] != 0]
df_clean = df_clean.reset_index(drop = True)
df_clean

연도  월  주차    긍정    부정  잘모름  과학_IT    경제    국제  북한_외교  ...        경제%  \
0    2012  1   1  26.0  63.0   11    334  1335   870    338  ...  15.272852   
1    2012  1   2  24.0  65.0   11    372  1464  1099    286  ...  15.743628   
2    2012  1   3  22.0  65.0   13    455  1500  1259    250  ...  14.414761   
3    2012  1   4  24.0  64.0   12    319  1066  1007    231  ...  14.318334   
4    2012  2   1  22.0  65.0   13    447  1628  1081    235  ...  15.570008   
..    ... ..  ..   ...   ...  ...    ...   ...   ...    ...  ...        ...   
533  2023  7   4  35.0  55.0   10    474  1591  1052    465  ...  12.859683   
534  2023  8   1  33.0  56.0   11    418  1462  1152    312  ...  12.703102   
535  2023  8   2  35.0  57.0    8    399  1244  1248    168  ...  10.445004   
536  2023  8   4  34.0  57.0    9    486  1497  1652    792  ...  12.125385   
537  2023  8   5  33.0  59.0    8    481  1602  1556    341  ...  13.070082   

           국제%    북한_외교%        문화%        사회%     사건_사고%        정치%  \
0     9.953095  3.866834  13.980094  13.259352   8.763299  11.943714   
1    11.818475  3.075600  12.216367  13.237983   8.506291  12.345413   
2    12.098789  2.402460  12.118009  13.213531   8.591197  12.742648   
3    13.525856  3.102754  12.397582  13.472129   8.623237  10.100739   
4    10.338562  2.247513  13.274675  13.771997   8.645754  11.027161   
..         ...       ...        ...        ...        ...        ...   
533   8.503071  3.758487   7.363401  17.119302  10.539929  10.483349   
534  10.009558  2.710922   7.863411  18.463811   8.523764  10.278912   
535  10.478589  1.410579   7.867338  15.633921  12.216625   8.413098   
536  13.380852  6.415033   7.297910  13.672445  11.501701   9.881743   
537  12.694787  2.782084   8.411520  13.641185  10.777515  13.045607   

         스포츠%        지역%  기타(날씨, 미분류)%  
0    6.475232   6.784121      5.880334  
1    6.538337   6.645876      5.871599  
2    6.409764   7.120892      6.515472  
3    6.662189   6.675621      6.836803  
4    7.067712   7.096404      6.685157  
..        ...        ...           ...  
533  4.704171  14.354995      6.482380  
534  4.674602  13.293944      7.846034  
535  3.912678  13.853904     12.418136  
536  4.122793  12.214482      5.451158  
537  3.875337  12.278698      5.498899  

[538 rows x 29 columns]

In [12]:
df_clean.columns

Index(['연도', '월', '주차', '긍정', '부정', '잘모름', '과학_IT', '경제', '국제', '북한_외교', '문화',
       '사회', '사건_사고', '정치', '스포츠', '지역', '기타(날씨, 미분류)', '주간합', '과학_IT%', '경제%',
       '국제%', '북한_외교%', '문화%', '사회%', '사건_사고%', '정치%', '스포츠%', '지역%',
       '기타(날씨, 미분류)%'],
      dtype='object')

In [13]:
len(df_clean)

538

In [14]:
## 전월 긍정_부정_잘모름 열 추가
for i in range(1,len(df_clean)):
    df_clean.loc[i,'긍정_과거'] = df_clean.loc[i-1,'긍정']
    df_clean.loc[i,'부정_과거'] = df_clean.loc[i-1,'부정']
    df_clean.loc[i,'잘모름_과거'] = df_clean.loc[i-1,'잘모름']
    
    ## 뉴스 카테고리별 증감량 열 추가
    df_clean.loc[i,'과학_IT_증감량'] = df_clean.loc[i,'과학_IT'] - df_clean.loc[i-1,'과학_IT']
    df_clean.loc[i,'경제_증감량'] = df_clean.loc[i,'경제'] - df_clean.loc[i-1,'경제']
    df_clean.loc[i,'국제_증감량'] = df_clean.loc[i,'국제'] - df_clean.loc[i-1,'국제']
    df_clean.loc[i,'북한_외교_증감량'] = df_clean.loc[i,'북한_외교'] - df_clean.loc[i-1,'북한_외교']
    df_clean.loc[i,'문화_증감량'] = df_clean.loc[i,'문화'] - df_clean.loc[i-1,'문화']
    df_clean.loc[i,'사회_증감량'] = df_clean.loc[i,'사회'] - df_clean.loc[i-1,'사회']
    df_clean.loc[i,'사건_사고_증감량'] = df_clean.loc[i,'사건_사고'] - df_clean.loc[i-1,'사건_사고']
    df_clean.loc[i,'정치_증감량'] = df_clean.loc[i,'정치'] - df_clean.loc[i-1,'정치']
    df_clean.loc[i,'스포츠_증감량'] = df_clean.loc[i,'스포츠'] - df_clean.loc[i-1,'스포츠']
    df_clean.loc[i,'지역_증감량'] = df_clean.loc[i,'지역'] - df_clean.loc[i-1,'지역']
    df_clean.loc[i,'기타(날씨, 미분류)_증감량'] = df_clean.loc[i,'기타(날씨, 미분류)'] - df_clean.loc[i-1,'기타(날씨, 미분류)']
    
    
    
df_clean = df_clean.drop(0,axis=0).reset_index(drop = True)

In [15]:
display(df_clean)

display(df_clean.columns)

연도  월  주차    긍정    부정  잘모름  과학_IT    경제    국제  북한_외교  ...  경제_증감량  \
0    2012  1   2  24.0  65.0   11    372  1464  1099    286  ...   129.0   
1    2012  1   3  22.0  65.0   13    455  1500  1259    250  ...    36.0   
2    2012  1   4  24.0  64.0   12    319  1066  1007    231  ...  -434.0   
3    2012  2   1  22.0  65.0   13    447  1628  1081    235  ...   562.0   
4    2012  2   2  24.0  64.0   12    382  1632  1239    260  ...     4.0   
..    ... ..  ..   ...   ...  ...    ...   ...   ...    ...  ...     ...   
532  2023  7   4  35.0  55.0   10    474  1591  1052    465  ...   195.0   
533  2023  8   1  33.0  56.0   11    418  1462  1152    312  ...  -129.0   
534  2023  8   2  35.0  57.0    8    399  1244  1248    168  ...  -218.0   
535  2023  8   4  34.0  57.0    9    486  1497  1652    792  ...   253.0   
536  2023  8   5  33.0  59.0    8    481  1602  1556    341  ...   105.0   

     국제_증감량  북한_외교_증감량  문화_증감량  사회_증감량  사건_사고_증감량  정치_증감량  스포츠_증감량  지역_증감량  \
0     229.0      -52.0   -86.0    72.0       25.0   104.0     42.0    25.0   
1     160.0      -36.0   125.0   144.0      103.0   178.0     59.0   123.0   
2    -252.0      -19.0  -338.0  -372.0     -252.0  -574.0   -171.0  -244.0   
3      74.0        4.0   465.0   437.0      262.0   401.0    243.0   245.0   
4     158.0       25.0   -66.0   -15.0      -67.0   160.0     67.0    -5.0   
..      ...        ...     ...     ...        ...     ...      ...     ...   
532  -141.0      -81.0    29.0  -156.0      417.0    62.0    130.0  -891.0   
533   100.0     -153.0    -6.0     7.0     -323.0  -114.0    -44.0  -246.0   
534    96.0     -144.0    32.0  -263.0      474.0  -181.0    -72.0   120.0   
535   404.0      624.0   -36.0  -174.0      -35.0   218.0     43.0  -142.0   
536   -96.0     -451.0   130.0   -16.0      -99.0   379.0    -34.0    -3.0   

     기타(날씨, 미분류)_증감량  
0               32.0  
1              132.0  
2             -169.0  
3              190.0  
4              -98.0  
..               ...  
532            -43.0  
533            101.0  
534            576.0  
535           -806.0  
536              1.0  

[537 rows x 43 columns]

Index(['연도', '월', '주차', '긍정', '부정', '잘모름', '과학_IT', '경제', '국제', '북한_외교', '문화',
       '사회', '사건_사고', '정치', '스포츠', '지역', '기타(날씨, 미분류)', '주간합', '과학_IT%', '경제%',
       '국제%', '북한_외교%', '문화%', '사회%', '사건_사고%', '정치%', '스포츠%', '지역%',
       '기타(날씨, 미분류)%', '긍정_과거', '부정_과거', '잘모름_과거', '과학_IT_증감량', '경제_증감량',
       '국제_증감량', '북한_외교_증감량', '문화_증감량', '사회_증감량', '사건_사고_증감량', '정치_증감량',
       '스포츠_증감량', '지역_증감량', '기타(날씨, 미분류)_증감량'],
      dtype='object')

In [16]:
# 학습용 데이터
X_train = df_clean.loc[df_clean['연도'] < 2023,['긍정_과거', '부정_과거', '잘모름_과거', '과학_IT', '경제', '국제', '북한_외교', '문화',
       '사회', '사건_사고', '정치', '스포츠', '지역', '기타(날씨, 미분류)', '주간합', '과학_IT%', '경제%',
       '국제%', '북한_외교%', '문화%', '사회%', '사건_사고%', '정치%', '스포츠%', '지역%', '기타(날씨, 미분류)%',
        '과학_IT_증감량', '경제_증감량', '국제_증감량', '북한_외교_증감량', '문화_증감량', '사회_증감량', '사건_사고_증감량', '정치_증감량',
       '스포츠_증감량', '지역_증감량', '기타(날씨, 미분류)_증감량']]

y_train = df_clean.loc[df_clean['연도'] < 2023,['긍정']]

# y_train = df_clean.loc[df_clean['연도'] < 2022,['부정']]

# 테스트용 데이터
X_test = df_clean.loc[df_clean['연도'] == 2023,['긍정_과거', '부정_과거', '잘모름_과거','과학_IT', '경제', '국제', '북한_외교', '문화',
       '사회', '사건_사고', '정치', '스포츠', '지역', '기타(날씨, 미분류)', '주간합', '과학_IT%', '경제%',
       '국제%', '북한_외교%', '문화%', '사회%', '사건_사고%', '정치%', '스포츠%', '지역%', '기타(날씨, 미분류)%',
         '과학_IT_증감량', '경제_증감량', '국제_증감량', '북한_외교_증감량', '문화_증감량', '사회_증감량', '사건_사고_증감량', '정치_증감량',
       '스포츠_증감량', '지역_증감량', '기타(날씨, 미분류)_증감량']]
y_test = df_clean.loc[df_clean['연도'] == 2023,['긍정']]

# y_test = df_clean.loc[df_clean['연도'] == 2022,['부정']]

y_idx = df_clean.loc[df_clean['연도'] == 2023,['연도', '월', '주차']]

In [17]:
y_test

긍정
505  37.0
506  35.0
507  36.0
508  34.0
509  32.0
510  35.0
511  37.0
512  36.0
513  34.0
514  33.0
515  34.0
516  30.0
517  31.0
518  27.0
519  31.0
520  30.0
521  33.0
522  35.0
523  37.0
524  36.0
525  35.0
526  35.0
527  36.0
528  36.0
529  38.0
530  32.0
531  33.0
532  35.0
533  33.0
534  35.0
535  34.0
536  33.0

In [18]:
X_train.columns = ["Positive_Past","Negative_Past","Non_Past","Science_IT","Ecnomic","Global","North_Korea","Culture","Social","Issue", 'Politic', 'Sports', 'Local', 'Etc', 'SUM',
                  "Science_IT_P","Ecnomic_P","Global_P","North_Korea_P","Culture_P","Social_P","Issue_P", 'Politic_P', 'Sports_P', 'Local_P', 'Etc_P',
                  "Science_IT_ID","Ecnomic_ID","Global_ID","North_Korea_ID","Culture_ID","Social_ID","Issue_ID", 'Politic_ID', 'Sports_ID', 'Local_ID', 'Etc_ID']
y_train.columns = ['Target']

X_test.columns = ["Positive_Past","Negative_Past","Non_Past","Science_IT","Ecnomic","Global","North_Korea","Culture","Social","Issue", 'Politic', 'Sports', 'Local', 'Etc', 'SUM',
                  "Science_IT_P","Ecnomic_P","Global_P","North_Korea_P","Culture_P","Social_P","Issue_P", 'Politic_P', 'Sports_P', 'Local_P', 'Etc_P',
                  "Science_IT_ID","Ecnomic_ID","Global_ID","North_Korea_ID","Culture_ID","Social_ID","Issue_ID", 'Politic_ID', 'Sports_ID', 'Local_ID', 'Etc_ID']
y_test.columns = ['Target']

## 3-1. LinearRegression

In [19]:
from sklearn.linear_model import LinearRegression
lr_model = LinearRegression()

lr_model.fit(X_train,y_train)

LinearRegression()

In [20]:
y_pred_lr = lr_model.predict(X_test)
y_pred_lr_df = pd.DataFrame(y_pred_lr,columns=['y_pred_LinearRegression'])
y_pred_lr_df

y_pred_LinearRegression
0                 38.120605
1                 34.481567
2                 33.891602
3                 34.900269
4                 33.912842
5                 31.233398
6                 35.751343
7                 36.994263
8                 35.930542
9                 35.173828
10                33.924194
11                33.546265
12                29.269409
13                30.706055
14                27.916382
15                32.699829
16                29.942749
17                34.066528
18                34.289551
19                38.297119
20                37.249390
21                34.829346
22                34.352173
23                35.885864
24                35.462891
25                38.067993
26                33.115356
27                32.012939
28                35.040527
29                30.693970
30                36.332764
31                33.722290

In [21]:
## 결과 취합

result = pd.DataFrame([y_test.Target]).T.reset_index(drop = True)
result = pd.concat([y_idx.reset_index(drop=True),result,y_pred_lr_df],axis = 1)
result

연도  월  주차  Target  y_pred_LinearRegression
0   2023  1   1    37.0                38.120605
1   2023  1   2    35.0                34.481567
2   2023  1   3    36.0                33.891602
3   2023  2   1    34.0                34.900269
4   2023  2   2    32.0                33.912842
5   2023  2   3    35.0                31.233398
6   2023  2   4    37.0                35.751343
7   2023  3   1    36.0                36.994263
8   2023  3   2    34.0                35.930542
9   2023  3   3    33.0                35.173828
10  2023  3   4    34.0                33.924194
11  2023  3   5    30.0                33.546265
12  2023  4   1    31.0                29.269409
13  2023  4   2    27.0                30.706055
14  2023  4   3    31.0                27.916382
15  2023  4   4    30.0                32.699829
16  2023  5   1    33.0                29.942749
17  2023  5   2    35.0                34.066528
18  2023  5   3    37.0                34.289551
19  2023  5   4    36.0                38.297119
20  2023  6   1    35.0                37.249390
21  2023  6   3    35.0                34.829346
22  2023  6   4    36.0                34.352173
23  2023  6   5    36.0                35.885864
24  2023  7   1    38.0                35.462891
25  2023  7   2    32.0                38.067993
26  2023  7   3    33.0                33.115356
27  2023  7   4    35.0                32.012939
28  2023  8   1    33.0                35.040527
29  2023  8   2    35.0                30.693970
30  2023  8   4    34.0                36.332764
31  2023  8   5    33.0                33.722290

## 3-2. DecisionTree

In [22]:
from sklearn.tree import DecisionTreeRegressor

dt_model = DecisionTreeRegressor()

dt_model.fit(X_train, y_train)

DecisionTreeRegressor()

In [23]:
y_pred_dt = dt_model.predict(X_test)
y_pred_dt_df = pd.DataFrame(y_pred_dt,columns=['y_pred_DecisionTreeRegressor'])
y_pred_dt_df

result = pd.concat([result,y_pred_dt_df],axis = 1)
result

연도  월  주차  Target  y_pred_LinearRegression  y_pred_DecisionTreeRegressor
0   2023  1   1    37.0                38.120605                          38.0
1   2023  1   2    35.0                34.481567                          38.0
2   2023  1   3    36.0                33.891602                          32.0
3   2023  2   1    34.0                34.900269                          38.0
4   2023  2   2    32.0                33.912842                          37.0
5   2023  2   3    35.0                31.233398                          30.0
6   2023  2   4    37.0                35.751343                          32.0
7   2023  3   1    36.0                36.994263                          37.0
8   2023  3   2    34.0                35.930542                          38.0
9   2023  3   3    33.0                35.173828                          32.0
10  2023  3   4    34.0                33.924194                          29.0
11  2023  3   5    30.0                33.546265                          33.0
12  2023  4   1    31.0                29.269409                          29.0
13  2023  4   2    27.0                30.706055                          30.0
14  2023  4   3    31.0                27.916382                          33.0
15  2023  4   4    30.0                32.699829                          29.0
16  2023  5   1    33.0                29.942749                          30.0
17  2023  5   2    35.0                34.066528                          31.0
18  2023  5   3    37.0                34.289551                          32.0
19  2023  5   4    36.0                38.297119                          40.0
20  2023  6   1    35.0                37.249390                          38.0
21  2023  6   3    35.0                34.829346                          37.0
22  2023  6   4    36.0                34.352173                          32.0
23  2023  6   5    36.0                35.885864                          38.0
24  2023  7   1    38.0                35.462891                          38.0
25  2023  7   2    32.0                38.067993                          38.0
26  2023  7   3    33.0                33.115356                          29.0
27  2023  7   4    35.0                32.012939                          36.0
28  2023  8   1    33.0                35.040527                          30.0
29  2023  8   2    35.0                30.693970                          30.0
30  2023  8   4    34.0                36.332764                          37.0
31  2023  8   5    33.0                33.722290                          32.0

## 3-3. RandomForest

In [24]:
from sklearn.ensemble import RandomForestRegressor

rf_model = RandomForestRegressor()

rf_model.fit(X_train, y_train)

C:\Users\user\AppData\Local\Temp\ipykernel_23404\371921194.py:5: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  rf_model.fit(X_train, y_train)


RandomForestRegressor()

In [25]:
y_pred_rf = rf_model.predict(X_test)
y_pred_rf_df = pd.DataFrame(y_pred_rf,columns=['y_pred_RandomForestRegressor'])
y_pred_rf_df

y_pred_RandomForestRegressor
0                          39.39
1                          37.73
2                          34.76
3                          37.49
4                          34.57
5                          31.09
6                          36.25
7                          36.98
8                          36.92
9                          34.53
10                         31.38
11                         34.55
12                         30.84
13                         30.64
14                         26.60
15                         31.40
16                         30.27
17                         31.43
18                         34.55
19                         38.28
20                         39.44
21                         35.18
22                         36.15
23                         38.48
24                         38.03
25                         39.61
26                         31.29
27                         31.66
28                         35.70
29                         31.43
30                         36.65
31                         33.87

In [26]:
## 결과 취합

result = pd.concat([result,y_pred_rf_df],axis = 1)
result

연도  월  주차  Target  y_pred_LinearRegression  \
0   2023  1   1    37.0                38.120605   
1   2023  1   2    35.0                34.481567   
2   2023  1   3    36.0                33.891602   
3   2023  2   1    34.0                34.900269   
4   2023  2   2    32.0                33.912842   
5   2023  2   3    35.0                31.233398   
6   2023  2   4    37.0                35.751343   
7   2023  3   1    36.0                36.994263   
8   2023  3   2    34.0                35.930542   
9   2023  3   3    33.0                35.173828   
10  2023  3   4    34.0                33.924194   
11  2023  3   5    30.0                33.546265   
12  2023  4   1    31.0                29.269409   
13  2023  4   2    27.0                30.706055   
14  2023  4   3    31.0                27.916382   
15  2023  4   4    30.0                32.699829   
16  2023  5   1    33.0                29.942749   
17  2023  5   2    35.0                34.066528   
18  2023  5   3    37.0                34.289551   
19  2023  5   4    36.0                38.297119   
20  2023  6   1    35.0                37.249390   
21  2023  6   3    35.0                34.829346   
22  2023  6   4    36.0                34.352173   
23  2023  6   5    36.0                35.885864   
24  2023  7   1    38.0                35.462891   
25  2023  7   2    32.0                38.067993   
26  2023  7   3    33.0                33.115356   
27  2023  7   4    35.0                32.012939   
28  2023  8   1    33.0                35.040527   
29  2023  8   2    35.0                30.693970   
30  2023  8   4    34.0                36.332764   
31  2023  8   5    33.0                33.722290   

    y_pred_DecisionTreeRegressor  y_pred_RandomForestRegressor  
0                           38.0                         39.39  
1                           38.0                         37.73  
2                           32.0                         34.76  
3                           38.0                         37.49  
4                           37.0                         34.57  
5                           30.0                         31.09  
6                           32.0                         36.25  
7                           37.0                         36.98  
8                           38.0                         36.92  
9                           32.0                         34.53  
10                          29.0                         31.38  
11                          33.0                         34.55  
12                          29.0                         30.84  
13                          30.0                         30.64  
14                          33.0                         26.60  
15                          29.0                         31.40  
16                          30.0                         30.27  
17                          31.0                         31.43  
18                          32.0                         34.55  
19                          40.0                         38.28  
20                          38.0                         39.44  
21                          37.0                         35.18  
22                          32.0                         36.15  
23                          38.0                         38.48  
24                          38.0                         38.03  
25                          38.0                         39.61  
26                          29.0                         31.29  
27                          36.0                         31.66  
28                          30.0                         35.70  
29                          30.0                         31.43  
30                          37.0                         36.65  
31                          32.0                         33.87

## 3-4. LightGBM

In [27]:
from lightgbm import LGBMRegressor

## 모델링

lgbm_model = LGBMRegressor()
lgbm_model.fit(X_train,y_train)

lgbm_model.score(X_train,y_train)

0.991345352211649

In [28]:
y_pred_lgbm = lgbm_model.predict(X_test)
y_pred_lgbm_df = pd.DataFrame(y_pred_lgbm,columns=['y_pred_LGBMRegressor'])
y_pred_lgbm_df

y_pred_LGBMRegressor
0              38.866138
1              36.470950
2              36.196506
3              36.787965
4              36.485461
5              33.917688
6              37.443942
7              35.861967
8              35.177011
9              35.417410
10             32.565522
11             35.724533
12             32.799433
13             32.206817
14             25.101331
15             31.474708
16             30.324103
17             33.254655
18             35.290503
19             38.196475
20             38.612672
21             37.314782
22             36.028791
23             37.664158
24             36.558642
25             37.338596
26             31.865494
27             30.978240
28             36.846281
29             30.783460
30             37.696456
31             35.469863

In [29]:
## 결과 취합

result = pd.concat([result,y_pred_lgbm_df],axis = 1)
result

연도  월  주차  Target  y_pred_LinearRegression  \
0   2023  1   1    37.0                38.120605   
1   2023  1   2    35.0                34.481567   
2   2023  1   3    36.0                33.891602   
3   2023  2   1    34.0                34.900269   
4   2023  2   2    32.0                33.912842   
5   2023  2   3    35.0                31.233398   
6   2023  2   4    37.0                35.751343   
7   2023  3   1    36.0                36.994263   
8   2023  3   2    34.0                35.930542   
9   2023  3   3    33.0                35.173828   
10  2023  3   4    34.0                33.924194   
11  2023  3   5    30.0                33.546265   
12  2023  4   1    31.0                29.269409   
13  2023  4   2    27.0                30.706055   
14  2023  4   3    31.0                27.916382   
15  2023  4   4    30.0                32.699829   
16  2023  5   1    33.0                29.942749   
17  2023  5   2    35.0                34.066528   
18  2023  5   3    37.0                34.289551   
19  2023  5   4    36.0                38.297119   
20  2023  6   1    35.0                37.249390   
21  2023  6   3    35.0                34.829346   
22  2023  6   4    36.0                34.352173   
23  2023  6   5    36.0                35.885864   
24  2023  7   1    38.0                35.462891   
25  2023  7   2    32.0                38.067993   
26  2023  7   3    33.0                33.115356   
27  2023  7   4    35.0                32.012939   
28  2023  8   1    33.0                35.040527   
29  2023  8   2    35.0                30.693970   
30  2023  8   4    34.0                36.332764   
31  2023  8   5    33.0                33.722290   

    y_pred_DecisionTreeRegressor  y_pred_RandomForestRegressor  \
0                           38.0                         39.39   
1                           38.0                         37.73   
2                           32.0                         34.76   
3                           38.0                         37.49   
4                           37.0                         34.57   
5                           30.0                         31.09   
6                           32.0                         36.25   
7                           37.0                         36.98   
8                           38.0                         36.92   
9                           32.0                         34.53   
10                          29.0                         31.38   
11                          33.0                         34.55   
12                          29.0                         30.84   
13                          30.0                         30.64   
14                          33.0                         26.60   
15                          29.0                         31.40   
16                          30.0                         30.27   
17                          31.0                         31.43   
18                          32.0                         34.55   
19                          40.0                         38.28   
20                          38.0                         39.44   
21                          37.0                         35.18   
22                          32.0                         36.15   
23                          38.0                         38.48   
24                          38.0                         38.03   
25                          38.0                         39.61   
26                          29.0                         31.29   
27                          36.0                         31.66   
28                          30.0                         35.70   
29                          30.0                         31.43   
30                          37.0                         36.65   
31                          32.0                         33.87   

    y_pred_LGBMRegressor  
0              38.866138  
1              36.470950  
2              36.196506  
3 

## 3-5. ExplainableBoostingModel


In [30]:
from interpret.glassbox import ExplainableBoostingRegressor
ebm_model = ExplainableBoostingRegressor()
ebm_model.fit(X_train, y_train)

ExplainableBoostingRegressor(feature_names=['Positive_Past', 'Negative_Past',
                                            'Non_Past', 'Science_IT', 'Ecnomic',
                                            'Global', 'North_Korea', 'Culture',
                                            'Social', 'Issue', 'Politic',
                                            'Sports', 'Local', 'Etc', 'SUM',
                                            'Science_IT_P', 'Ecnomic_P',
                                            'Global_P', 'North_Korea_P',
                                            'Culture_P', 'Social_P', 'Issue_P',
                                            'Politic_P', 'Sports_P', 'Local_P',
                                            'Etc_P', 'Science_IT_ID',
                                            'Ecnomi...
                                            'continuous', 'continuous',
                                            'continuous', 'continuous',
                                   

In [31]:
from interpret import set_visualize_provider
from interpret.provider import InlineProvider
set_visualize_provider(InlineProvider())

In [32]:
from interpret import show
show(ebm_model.explain_global())

In [33]:
show(ebm_model.explain_local(X_test[:5], y_test[:5]), 0)

In [34]:
y_pred_ebm = ebm_model.predict(X_test)
y_pred_ebm_df = pd.DataFrame(y_pred_ebm,columns=['y_pred_ExplainableBoostingRegressor'])
y_pred_ebm_df

y_pred_ExplainableBoostingRegressor
0                             39.735873
1                             43.772738
2                             33.894910
3                             38.753155
4                             37.795112
5                             29.033625
6                             38.487803
7                             36.153664
8                             30.958486
9                             35.770671
10                            34.373128
11                            34.746438
12                            31.204493
13                            34.762800
14                            30.346724
15                            35.111527
16                            34.179654
17                            32.943775
18                            33.358703
19                            36.418413
20                            41.233105
21                            37.998188
22                            35.475192
23                            34.084038
24                            37.070042
25                            35.294506
26                            33.389309
27                            31.720858
28                            33.588752
29                            26.534918
30                            39.300791
31                            33.382276

In [35]:
## 결과 취합

result = pd.concat([result,y_pred_ebm_df],axis = 1)
result

연도  월  주차  Target  y_pred_LinearRegression  \
0   2023  1   1    37.0                38.120605   
1   2023  1   2    35.0                34.481567   
2   2023  1   3    36.0                33.891602   
3   2023  2   1    34.0                34.900269   
4   2023  2   2    32.0                33.912842   
5   2023  2   3    35.0                31.233398   
6   2023  2   4    37.0                35.751343   
7   2023  3   1    36.0                36.994263   
8   2023  3   2    34.0                35.930542   
9   2023  3   3    33.0                35.173828   
10  2023  3   4    34.0                33.924194   
11  2023  3   5    30.0                33.546265   
12  2023  4   1    31.0                29.269409   
13  2023  4   2    27.0                30.706055   
14  2023  4   3    31.0                27.916382   
15  2023  4   4    30.0                32.699829   
16  2023  5   1    33.0                29.942749   
17  2023  5   2    35.0                34.066528   
18  2023  5   3    37.0                34.289551   
19  2023  5   4    36.0                38.297119   
20  2023  6   1    35.0                37.249390   
21  2023  6   3    35.0                34.829346   
22  2023  6   4    36.0                34.352173   
23  2023  6   5    36.0                35.885864   
24  2023  7   1    38.0                35.462891   
25  2023  7   2    32.0                38.067993   
26  2023  7   3    33.0                33.115356   
27  2023  7   4    35.0                32.012939   
28  2023  8   1    33.0                35.040527   
29  2023  8   2    35.0                30.693970   
30  2023  8   4    34.0                36.332764   
31  2023  8   5    33.0                33.722290   

    y_pred_DecisionTreeRegressor  y_pred_RandomForestRegressor  \
0                           38.0                         39.39   
1                           38.0                         37.73   
2                           32.0                         34.76   
3                           38.0                         37.49   
4                           37.0                         34.57   
5                           30.0                         31.09   
6                           32.0                         36.25   
7                           37.0                         36.98   
8                           38.0                         36.92   
9                           32.0                         34.53   
10                          29.0                         31.38   
11                          33.0                         34.55   
12                          29.0                         30.84   
13                          30.0                         30.64   
14                          33.0                         26.60   
15                          29.0                         31.40   
16                          30.0                         30.27   
17                          31.0                         31.43   
18                          32.0                         34.55   
19                          40.0                         38.28   
20                          38.0                         39.44   
21                          37.0                         35.18   
22                          32.0                         36.15   
23                          38.0                         38.48   
24                          38.0                         38.03   
25                          38.0                         39.61   
26                          29.0                         31.29   
27                          36.0                         31.66   
28                          30.0                         35.70   
29                          30.0                         31.43   
30                          37.0                         36.65   
31                          32.0                         33.87   

    y_pred_LGBMRegressor  y_pred_ExplainableBoostingRegressor  
0              38.866138                      

In [36]:
result.to_csv("모델링_결과.csv", index = False, encoding = 'cp949')

### 4. 성능 비교

In [37]:
## 성능 지표 확인
from sklearn.metrics import mean_absolute_error

lr_metric_score = mean_absolute_error(y_pred_lr, y_test.Target)
dt_metric_score = mean_absolute_error(y_pred_dt, y_test.Target)
rf_metric_score = mean_absolute_error(y_pred_rf, y_test.Target)
lgbm_metric_score = mean_absolute_error(y_pred_lgbm, y_test.Target)
ebm_metric_score = mean_absolute_error(y_pred_ebm, y_test.Target)

display(lr_metric_score)
display(dt_metric_score)
display(rf_metric_score)
display(lgbm_metric_score)
display(ebm_metric_score)

2.056438446044922

3.09375

2.5012499999999998

2.491166933187176

3.0634726450192513